### ML Pipeline Preparation

Follow the instructions below to help you create your ML pipeline.
1. Import libraries and load data from database.

    Import Python libraries
    Load dataset from database with read_sql_table
    Define feature and target variables X and Y



In [1]:
# import libraries
import pandas as pd
import numpy as np
from sqlalchemy import create_engine


In [2]:
from sklearn.pipeline import Pipeline
from sklearn.feature_extraction.text import CountVectorizer, TfidfTransformer
from sklearn.multioutput import MultiOutputClassifier
from sklearn.neighbors import KNeighborsClassifier
from sklearn.datasets import make_multilabel_classification
from sklearn.model_selection import train_test_split, GridSearchCV
from sklearn.ensemble import RandomForestClassifier
from sklearn.metrics import accuracy_score
from sklearn.metrics import confusion_matrix

In [3]:
# load data from database
engine = create_engine('sqlite:///DisasterResponse.db')
df = pd.read_sql_table('DisasterResponse', engine)

In [4]:
df.head()

id                                            message  \
0   2  Weather update - a cold front from Cuba that c...   
1   7            Is the Hurricane over or is it not over   
2   8                    Looking for someone but no name   
3   9  UN reports Leogane 80-90 destroyed. Only Hospi...   
4  12  says: west side of Haiti, rest of the country ...   

                                            original   genre  related  \
0  Un front froid se retrouve sur Cuba ce matin. ...  direct        1   
1                 Cyclone nan fini osinon li pa fini  direct        1   
2  Patnm, di Maryani relem pou li banm nouvel li ...  direct        1   
3  UN reports Leogane 80-90 destroyed. Only Hospi...  direct        1   
4  facade ouest d Haiti et le reste du pays aujou...  direct        1   

   request  offer  aid_related  medical_help  medical_products  ...  \
0        0      0            0             0                 0  ...   
1        0      0            1             0                 0  ...   
2        0      0            0             0                 0  ...   
3        1      0            1             0                 1  ...   
4        0      0            0             0                 0  ...   

   aid_centers  other_infrastructure  weather_related  floods  storm  fire  \
0            0                     0                0       0      0     0   
1            0                     0                1       0      1     0   
2            0                     0                0       0      0     0   
3            0                     0                0       0      0     0   
4            0                     0                0       0      0     0   

   earthquake  cold  other_weather  direct_report  
0           0     0              0              0  
1           0     0              0              0  
2           0     0              0              0  
3           0     0              0              0  
4           0     0              0              0  

[5 rows x 40 columns]

In [5]:
df.describe()

id       related       request         offer   aid_related  \
count  26216.00000  26216.000000  26216.000000  26216.000000  26216.000000   
mean   15224.82133      0.773650      0.170659      0.004501      0.414251   
std     8826.88914      0.435276      0.376218      0.066940      0.492602   
min        2.00000      0.000000      0.000000      0.000000      0.000000   
25%     7446.75000      1.000000      0.000000      0.000000      0.000000   
50%    15662.50000      1.000000      0.000000      0.000000      0.000000   
75%    22924.25000      1.000000      0.000000      0.000000      1.000000   
max    30265.00000      2.000000      1.000000      1.000000      1.000000   

       medical_help  medical_products  search_and_rescue      security  \
count  26216.000000      26216.000000       26216.000000  26216.000000   
mean       0.079493          0.050084           0.027617      0.017966   
std        0.270513          0.218122           0.163875      0.132831   
min        0.000000          0.000000           0.000000      0.000000   
25%        0.000000          0.000000           0.000000      0.000000   
50%        0.000000          0.000000           0.000000      0.000000   
75%        0.000000          0.000000           0.000000      0.000000   
max        1.000000          1.000000           1.000000      1.000000   

           military  ...   aid_centers  other_infrastructure  weather_related  \
count  26216.000000  ...  26216.000000          26216.000000     26216.000000   
mean       0.032804  ...      0.011787              0.043904         0.278341   
std        0.178128  ...      0.107927              0.204887         0.448191   
min        0.000000  ...      0.000000              0.000000         0.000000   
25%        0.000000  ...      0.000000              0.000000         0.000000   
50%        0.000000  ...      0.000000              0.000000         0.000000   
75%        0.000000  ...      0.000000              0.000000         1.000000   
max        1.000000  ...      1.000000              1.000000         1.000000   

             floods         storm          fire    earthquake          cold  \
count  26216.000000  26216.000000  26216.000000  26216.000000  26216.000000   
mean       0.082202      0.093187      0.010757      0.093645      0.020217   
std        0.274677      0.290700      0.103158      0.291340      0.140743   
min        0.000000      0.000000      0.000000      0.000000      0.000000   
25%        0.000000      0.000000      0.000000      0.000000      0.000000   
50%        0.000000      0.000000      0.000000      0.000000      0.000000   
75%        0.000000      0.000000      0.000000      0.000000      0.000000   
max        1.000000      1.000000      1.000000      1.000000      1.000000   

       other_weather  direct_report  
count   26216.000000   26216.000000  
mean        0.052487       0.193584  
std         0.223011       0.395114  
min         0.000000       0.000000  
25%         0.000000       0.000000  
50%         0.000000       0.000000  
75%         0.000000       0.000000  
max         1.000000       1.000000  

[8 rows x 37 columns]

In [74]:
df.related.value_counts()

1    20094
0     6122
Name: related, dtype: int64

In [7]:
df['related'] = df.related.map(lambda x: 1 if x==2 else x)

In [8]:
df.related.value_counts()

1    20094
0     6122
Name: related, dtype: int64

In [9]:
# create a copy to work on
df_copy = df.copy(deep=False)

In [69]:
# since the identification of the message is considered the target, the message must be the feature.  
# assign the message to x
X = df_copy.message
y = df_copy.iloc[:,4:]

In [70]:
X.head()

0    Weather update - a cold front from Cuba that c...
1              Is the Hurricane over or is it not over
2                      Looking for someone but no name
3    UN reports Leogane 80-90 destroyed. Only Hospi...
4    says: west side of Haiti, rest of the country ...
Name: message, dtype: object

In [71]:
y.head()

related  request  offer  aid_related  medical_help  medical_products  \
0        1        0      0            0             0                 0   
1        1        0      0            1             0                 0   
2        1        0      0            0             0                 0   
3        1        1      0            1             0                 1   
4        1        0      0            0             0                 0   

   search_and_rescue  security  military  child_alone  ...  aid_centers  \
0                  0         0         0            0  ...            0   
1                  0         0         0            0  ...            0   
2                  0         0         0            0  ...            0   
3                  0         0         0            0  ...            0   
4                  0         0         0            0  ...            0   

   other_infrastructure  weather_related  floods  storm  fire  earthquake  \
0                     0                0       0      0     0           0   
1                     0                1       0      1     0           0   
2                     0                0       0      0     0           0   
3                     0                0       0      0     0           0   
4                     0                0       0      0     0           0   

   cold  other_weather  direct_report  
0     0              0              0  
1     0              0              0  
2     0              0              0  
3     0              0              0  
4     0              0              0  

[5 rows x 36 columns]

In [72]:
df_copy.related.unique()

array([1, 0], dtype=int64)

In [14]:
import nltk
nltk.download(['punkt', 'wordnet', 'averaged_perceptron_tagger'])
import re
from nltk.tokenize import word_tokenize
from nltk.stem import WordNetLemmatizer

[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\dsbb1\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package wordnet to
[nltk_data]     C:\Users\dsbb1\AppData\Roaming\nltk_data...
[nltk_data]   Package wordnet is already up-to-date!
[nltk_data] Downloading package averaged_perceptron_tagger to
[nltk_data]     C:\Users\dsbb1\AppData\Roaming\nltk_data...
[nltk_data]   Package averaged_perceptron_tagger is already up-to-
[nltk_data]       date!


In [73]:
def tokenize(text):
    # make text lower case
    text.lower()
    # Remove punctuation characters
    text = re.sub(r"[^a-zA-Z0-9]", " ", text)
    tokens = word_tokenize(text)
    lemmatizer = WordNetLemmatizer()

    clean_tokens = []
    for tok in tokens:
        clean_tok = lemmatizer.lemmatize(tok).lower().strip()
        clean_tokens.append(clean_tok)
    
    return clean_tokens

### 3. Build a machine learning pipeline

This machine pipeline should take in the message column as input and output classification results on the other 36 categories in the dataset. You may find the MultiOutputClassifier helpful for predicting multiple target variables.


In [16]:
pipeline = Pipeline([
        ('vect', CountVectorizer(tokenizer=tokenize)),
        ('tfidf', TfidfTransformer()),
        ('clf', MultiOutputClassifier(RandomForestClassifier()))
    ])

pipeline

Pipeline(memory=None,
         steps=[('vect',
                 CountVectorizer(analyzer='word', binary=False,
                                 decode_error='strict',
                                 dtype=<class 'numpy.int64'>, encoding='utf-8',
                                 input='content', lowercase=True, max_df=1.0,
                                 max_features=None, min_df=1,
                                 ngram_range=(1, 1), preprocessor=None,
                                 stop_words=None, strip_accents=None,
                                 token_pattern='(?u)\\b\\w\\w+\\b',
                                 tokenizer=<function tokenize at...
                                                                        ccp_alpha=0.0,
                                                                        class_weight=None,
                                                                        criterion='gini',
                                                                   

### 4. Train pipeline

    Split data into train and test sets
    Train pipeline



In [17]:
#using train_test_split, group the datea into training and test datasets
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.20, random_state=0)

In [18]:
# fits the pipeline created above to the training data
pipeline.fit(X_train, y_train)


Pipeline(memory=None,
         steps=[('vect',
                 CountVectorizer(analyzer='word', binary=False,
                                 decode_error='strict',
                                 dtype=<class 'numpy.int64'>, encoding='utf-8',
                                 input='content', lowercase=True, max_df=1.0,
                                 max_features=None, min_df=1,
                                 ngram_range=(1, 1), preprocessor=None,
                                 stop_words=None, strip_accents=None,
                                 token_pattern='(?u)\\b\\w\\w+\\b',
                                 tokenizer=<function tokenize at...
                                                                        ccp_alpha=0.0,
                                                                        class_weight=None,
                                                                        criterion='gini',
                                                                   

In [19]:
pipeline.get_params().keys()

dict_keys(['memory', 'steps', 'verbose', 'vect', 'tfidf', 'clf', 'vect__analyzer', 'vect__binary', 'vect__decode_error', 'vect__dtype', 'vect__encoding', 'vect__input', 'vect__lowercase', 'vect__max_df', 'vect__max_features', 'vect__min_df', 'vect__ngram_range', 'vect__preprocessor', 'vect__stop_words', 'vect__strip_accents', 'vect__token_pattern', 'vect__tokenizer', 'vect__vocabulary', 'tfidf__norm', 'tfidf__smooth_idf', 'tfidf__sublinear_tf', 'tfidf__use_idf', 'clf__estimator__bootstrap', 'clf__estimator__ccp_alpha', 'clf__estimator__class_weight', 'clf__estimator__criterion', 'clf__estimator__max_depth', 'clf__estimator__max_features', 'clf__estimator__max_leaf_nodes', 'clf__estimator__max_samples', 'clf__estimator__min_impurity_decrease', 'clf__estimator__min_impurity_split', 'clf__estimator__min_samples_leaf', 'clf__estimator__min_samples_split', 'clf__estimator__min_weight_fraction_leaf', 'clf__estimator__n_estimators', 'clf__estimator__n_jobs', 'clf__estimator__oob_score', 'clf_

### 6. Improve your model

Use grid search to find better parameters.


In [20]:
from sklearn.metrics import confusion_matrix
from sklearn.metrics import roc_auc_score
from sklearn.metrics import classification_report
from sklearn.datasets import make_multilabel_classification
from sklearn.svm import SVC

In [93]:
import nltk
nltk.download(['punkt', 'wordnet', 'averaged_perceptron_tagger'])

import re
import numpy as np
import pandas as pd
from nltk.tokenize import word_tokenize
from nltk.stem import WordNetLemmatizer

from sklearn.metrics import confusion_matrix
from sklearn.model_selection import GridSearchCV
from sklearn.ensemble import RandomForestClassifier
from sklearn.model_selection import train_test_split
from sklearn.pipeline import Pipeline, FeatureUnion
from sklearn.base import BaseEstimator, TransformerMixin
from sklearn.feature_extraction.text import CountVectorizer, TfidfTransformer


[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\dsbb1\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package wordnet to
[nltk_data]     C:\Users\dsbb1\AppData\Roaming\nltk_data...
[nltk_data]   Package wordnet is already up-to-date!
[nltk_data] Downloading package averaged_perceptron_tagger to
[nltk_data]     C:\Users\dsbb1\AppData\Roaming\nltk_data...
[nltk_data]   Package averaged_perceptron_tagger is already up-to-
[nltk_data]       date!


In [22]:
parameters = {
              'clf__estimator__n_estimators': [50,100],
             'clf__estimator__min_samples_split': [2,3]
            }
cv=GridSearchCV(pipeline, param_grid=parameters)

cv_fit = cv.fit(X_train,y_train)
print(cv_fit)

print(cv.score(X_train, y_train))


GridSearchCV(cv=None, error_score=nan,
             estimator=Pipeline(memory=None,
                                steps=[('vect',
                                        CountVectorizer(analyzer='word',
                                                        binary=False,
                                                        decode_error='strict',
                                                        dtype=<class 'numpy.int64'>,
                                                        encoding='utf-8',
                                                        input='content',
                                                        lowercase=True,
                                                        max_df=1.0,
                                                        max_features=None,
                                                        min_df=1,
                                                        ngram_range=(1, 1),
                                                        p

### 7. Test your model

Show the accuracy, precision, and recall of the tuned model.

Since this project focuses on code quality, process, and pipelines, there is no minimum performance metric needed to pass. However, make sure to fine tune your models for accuracy, precision and recall to make your project stand out - especially for your portfolio!


For testing accuracy, precision and recall, I referred to the the "Multi-output Classification Example with MultiOutputClassifier in Python" blog post in Data Tech Notes at the following url:  
https://www.datatechnotes.com/2020/03/multi-output-classification-with-multioutputclassifier.html


In [49]:
category_names = y.columns


y_pred = cv.predict(X_test)
print(classification_report(y_test, y_pred, target_names=category_names, zero_division=0))

                        precision    recall  f1-score   support

               related       0.82      0.97      0.89      4027
               request       0.90      0.44      0.59       911
                 offer       0.00      0.00      0.00        15
           aid_related       0.81      0.63      0.71      2202
          medical_help       0.63      0.03      0.05       420
      medical_products       0.95      0.07      0.14       258
     search_and_rescue       0.62      0.03      0.06       155
              security       0.00      0.00      0.00        94
              military       0.91      0.06      0.11       166
           child_alone       0.00      0.00      0.00         0
                 water       0.88      0.26      0.40       336
                  food       0.88      0.48      0.62       569
               shelter       0.87      0.27      0.41       467
              clothing       0.80      0.10      0.17        84
                 money       1.00      

In [48]:
 for i in range(len(category_names)):
        print("classification report for " + y_test.columns[i]
              , '\n', classification_report(y_test.values[:, i], y_pred[:, i])
              , '\n accuracy:', accuracy_score(y_test.values[:, i], y_pred[:, i]))

classification report for related 
               precision    recall  f1-score   support

           0       0.72      0.30      0.42      1217
           1       0.82      0.97      0.89      4027

    accuracy                           0.81      5244
   macro avg       0.77      0.63      0.65      5244
weighted avg       0.80      0.81      0.78      5244
 
 accuracy: 0.8104500381388253
classification report for request 
               precision    recall  f1-score   support

           0       0.89      0.99      0.94      4333
           1       0.90      0.44      0.59       911

    accuracy                           0.89      5244
   macro avg       0.90      0.71      0.76      5244
weighted avg       0.89      0.89      0.88      5244
 
 accuracy: 0.8935926773455377
classification report for offer 
               precision    recall  f1-score   support

           0       1.00      1.00      1.00      5229
           1       0.00      0.00      0.00        15

    accuracy  

classification report for buildings 
               precision    recall  f1-score   support

           0       0.95      1.00      0.98      4987
           1       0.75      0.06      0.11       257

    accuracy                           0.95      5244
   macro avg       0.85      0.53      0.54      5244
weighted avg       0.94      0.95      0.93      5244
 
 accuracy: 0.9528985507246377
classification report for electricity 
               precision    recall  f1-score   support

           0       0.98      1.00      0.99      5130
           1       0.67      0.04      0.07       114

    accuracy                           0.98      5244
   macro avg       0.82      0.52      0.53      5244
weighted avg       0.97      0.98      0.97      5244
 
 accuracy: 0.9786422578184591
classification report for tools 
               precision    recall  f1-score   support

           0       0.99      1.00      1.00      5201
           1       0.00      0.00      0.00        43

    accu

### 8. Try improving your model further. Here are a few ideas:

    try other machine learning algorithms
    add other features besides the TF-IDF




This attempt to improve the model uses StartingVerbExtractor.  The StartingVerbExtractor was shared with students during course training and is found at the following url: 
    https://classroom.udacity.com/nanodegrees/nd025/parts/3f1cdf90-8133-4822-ba56-934933b6b4bb/modules/fa5fdc5a-7de7-470f-81ba-ed37348de410/lessons/d64b867f-541b-491d-b704-b91abebab4d5/concepts/936b2739-c71b-467c-8988-562a72aeb1d1
    

In [80]:
from sklearn.base import BaseEstimator, TransformerMixin
from sklearn.pipeline import FeatureUnion

In [111]:
class StartingVerbExtractor(BaseEstimator, TransformerMixin):

    def starting_verb(self, text):
        sentence_list = nltk.sent_tokenize(text)
        for sentence in sentence_list:
            pos_tags = nltk.pos_tag(tokenize(sentence))
            first_word, first_tag = pos_tags[0]
            for z in range(10):
                print(pos_tags, first_word, first_tag)
                z = z+1
            if first_tag in ['VB', 'VBP'] or first_word == 'RT':
                return 1
        return 0

    
    def fit(self, x, y=None):
        return self

    def transform(self, X):
        X_tagged = pd.Series(X).apply(self.starting_verb)
        return pd.DataFrame(X_tagged)



In [ ]:
# create the pipeline that incorporates the FeatureUnion, CountVectorizer, TFID transformer, StartingVerbExtractor,  and
# RandomForest Classifiers
pipeline_v2 = Pipeline([
        ('features', FeatureUnion([

            ('text_pipeline', Pipeline([
                ('vect', CountVectorizer(tokenizer=tokenize)),
                ('tfidf', TfidfTransformer())
            ])),

            ('starting_verb', StartingVerbExtractor())
        ])),

        ('clf', MultiOutputClassifier(RandomForestClassifier()))
    ])

parameters = {
        'features__text_pipeline__vect__ngram_range': ((1, 1), (1, 2)),
         'clf__estimator__n_estimators': [50,100],
         'clf__estimator__min_samples_split': [2,3],
        'features__text_pipeline__tfidf__use_idf': (1, 0),
        'features__transformer_weights': (
            {'text_pipeline': 1, 'starting_verb': 0.5},
            {'text_pipeline': 0.5, 'starting_verb': 1},
            {'text_pipeline': 0.8, 'starting_verb': 1},
        )
    }

cv1 = GridSearchCV(pipeline_v2, param_grid=parameters)

cv1_fit = cv1.fit(X_train,y_train)
print(cv1_fit)

print(cv1.score(X_train, y_train))




[('the', 'DT'), ('french', 'JJ'), ('emergency', 'NN'), ('response', 'NN'), ('unit', 'NN'), ('is', 'VBZ'), ('active', 'JJ'), ('along', 'IN'), ('the', 'DT'), ('northeast', 'NN'), ('coast', 'NN'), ('providing', 'VBG'), ('water', 'NN'), ('to', 'TO'), ('14', 'CD'), ('000', 'CD'), ('idps', 'NN'), ('in', 'IN'), ('10', 'CD'), ('camp', 'NN'), ('in', 'IN'), ('samalanga', 'NN')] the DT
[('the', 'DT'), ('french', 'JJ'), ('emergency', 'NN'), ('response', 'NN'), ('unit', 'NN'), ('is', 'VBZ'), ('active', 'JJ'), ('along', 'IN'), ('the', 'DT'), ('northeast', 'NN'), ('coast', 'NN'), ('providing', 'VBG'), ('water', 'NN'), ('to', 'TO'), ('14', 'CD'), ('000', 'CD'), ('idps', 'NN'), ('in', 'IN'), ('10', 'CD'), ('camp', 'NN'), ('in', 'IN'), ('samalanga', 'NN')] the DT
[('the', 'DT'), ('french', 'JJ'), ('emergency', 'NN'), ('response', 'NN'), ('unit', 'NN'), ('is', 'VBZ'), ('active', 'JJ'), ('along', 'IN'), ('the', 'DT'), ('northeast', 'NN'), ('coast', 'NN'), ('providing', 'VBG'), ('water', 'NN'), ('to', 'TO'

[('meanwhile', 'RB'), ('a', 'DT'), ('two', 'CD'), ('year', 'NN'), ('old', 'JJ'), ('outbreak', 'NN'), ('of', 'IN'), ('cassava', 'NN'), ('brown', 'JJ'), ('streak', 'JJ'), ('disease', 'NN'), ('wa', 'NN'), ('of', 'IN'), ('growing', 'VBG'), ('concern', 'NN'), ('in', 'IN'), ('northern', 'JJ'), ('coastal', 'JJ'), ('area', 'NN'), ('fews', 'NNS'), ('warned', 'VBD')] meanwhile RB
[('meanwhile', 'RB'), ('a', 'DT'), ('two', 'CD'), ('year', 'NN'), ('old', 'JJ'), ('outbreak', 'NN'), ('of', 'IN'), ('cassava', 'NN'), ('brown', 'JJ'), ('streak', 'JJ'), ('disease', 'NN'), ('wa', 'NN'), ('of', 'IN'), ('growing', 'VBG'), ('concern', 'NN'), ('in', 'IN'), ('northern', 'JJ'), ('coastal', 'JJ'), ('area', 'NN'), ('fews', 'NNS'), ('warned', 'VBD')] meanwhile RB
[('meanwhile', 'RB'), ('a', 'DT'), ('two', 'CD'), ('year', 'NN'), ('old', 'JJ'), ('outbreak', 'NN'), ('of', 'IN'), ('cassava', 'NN'), ('brown', 'JJ'), ('streak', 'JJ'), ('disease', 'NN'), ('wa', 'NN'), ('of', 'IN'), ('growing', 'VBG'), ('concern', 'NN'),

[('iom', 'NN'), ('ha', 'NN'), ('further', 'RB'), ('committed', 'VBD'), ('itself', 'PRP'), ('to', 'TO'), ('fund', 'VB'), ('and', 'CC'), ('manage', 'VB'), ('the', 'DT'), ('rebuilding', 'NN'), ('equipping', 'NN'), ('and', 'CC'), ('commissioning', 'NN'), ('of', 'IN'), ('20', 'CD'), ('caring', 'VBG'), ('puskesmas', 'JJ'), ('level', 'NN'), ('community', 'NN'), ('health', 'NN'), ('clinic', 'NN'), ('with', 'IN'), ('10', 'CD'), ('inpatient', 'JJ'), ('bed', 'VBD'), ('each', 'DT'), ('to', 'TO'), ('serve', 'VB'), ('a', 'DT'), ('population', 'NN'), ('of', 'IN'), ('up', 'IN'), ('to', 'TO'), ('30', 'CD'), ('000', 'CD'), ('person', 'NN')] iom NN
[('iom', 'NN'), ('ha', 'NN'), ('further', 'RB'), ('committed', 'VBD'), ('itself', 'PRP'), ('to', 'TO'), ('fund', 'VB'), ('and', 'CC'), ('manage', 'VB'), ('the', 'DT'), ('rebuilding', 'NN'), ('equipping', 'NN'), ('and', 'CC'), ('commissioning', 'NN'), ('of', 'IN'), ('20', 'CD'), ('caring', 'VBG'), ('puskesmas', 'JJ'), ('level', 'NN'), ('community', 'NN'), ('hea

[('we', 'PRP'), ('are', 'VBP'), ('in', 'IN'), ('rue', 'JJ'), ('dessalines', 'NNS'), ('petit', 'VBP'), ('goaves', 'NNS'), ('and', 'CC'), ('it', 'PRP'), ('necessary', 'JJ'), ('to', 'TO')] we PRP
[('we', 'PRP'), ('are', 'VBP'), ('in', 'IN'), ('rue', 'JJ'), ('dessalines', 'NNS'), ('petit', 'VBP'), ('goaves', 'NNS'), ('and', 'CC'), ('it', 'PRP'), ('necessary', 'JJ'), ('to', 'TO')] we PRP
[('we', 'PRP'), ('are', 'VBP'), ('in', 'IN'), ('rue', 'JJ'), ('dessalines', 'NNS'), ('petit', 'VBP'), ('goaves', 'NNS'), ('and', 'CC'), ('it', 'PRP'), ('necessary', 'JJ'), ('to', 'TO')] we PRP
[('we', 'PRP'), ('are', 'VBP'), ('in', 'IN'), ('rue', 'JJ'), ('dessalines', 'NNS'), ('petit', 'VBP'), ('goaves', 'NNS'), ('and', 'CC'), ('it', 'PRP'), ('necessary', 'JJ'), ('to', 'TO')] we PRP
[('we', 'PRP'), ('are', 'VBP'), ('in', 'IN'), ('rue', 'JJ'), ('dessalines', 'NNS'), ('petit', 'VBP'), ('goaves', 'NNS'), ('and', 'CC'), ('it', 'PRP'), ('necessary', 'JJ'), ('to', 'TO')] we PRP
[('we', 'PRP'), ('are', 'VBP'), ('i

[('drinking', 'NN'), ('everytime', 'NN'), ('i', 'NN'), ('hear', 'VBP'), ('hurricane', 'NN'), ('sandy', 'NN'), ('east', 'JJ'), ('haven', 'NN'), ('or', 'CC'), ('new', 'JJ'), ('haven', 'VBN'), ('on', 'IN'), ('the', 'DT'), ('radio', 'NN'), ('alone', 'RB')] drinking NN
[('drinking', 'NN'), ('everytime', 'NN'), ('i', 'NN'), ('hear', 'VBP'), ('hurricane', 'NN'), ('sandy', 'NN'), ('east', 'JJ'), ('haven', 'NN'), ('or', 'CC'), ('new', 'JJ'), ('haven', 'VBN'), ('on', 'IN'), ('the', 'DT'), ('radio', 'NN'), ('alone', 'RB')] drinking NN
[('drinking', 'NN'), ('everytime', 'NN'), ('i', 'NN'), ('hear', 'VBP'), ('hurricane', 'NN'), ('sandy', 'NN'), ('east', 'JJ'), ('haven', 'NN'), ('or', 'CC'), ('new', 'JJ'), ('haven', 'VBN'), ('on', 'IN'), ('the', 'DT'), ('radio', 'NN'), ('alone', 'RB')] drinking NN
[('drinking', 'NN'), ('everytime', 'NN'), ('i', 'NN'), ('hear', 'VBP'), ('hurricane', 'NN'), ('sandy', 'NN'), ('east', 'JJ'), ('haven', 'NN'), ('or', 'CC'), ('new', 'JJ'), ('haven', 'VBN'), ('on', 'IN'), (

...

[('i', 'JJ'), ('d', 'VBP'), ('like', 'IN'), ('to', 'TO'), ('know', 'VB'), ('what', 'WP'), ('purpose', 'VB'), ('this', 'DT'), ('serf', 'NN')] i JJ
[('i', 'JJ'), ('d', 'VBP'), ('like', 'IN'), ('to', 'TO'), ('know', 'VB'), ('what', 'WP'), ('purpose', 'VB'), ('this', 'DT'), ('serf', 'NN')] i JJ
[('i', 'JJ'), ('d', 'VBP'), ('like', 'IN'), ('to', 'TO'), ('know', 'VB'), ('what', 'WP'), ('purpose', 'VB'), ('this', 'DT'), ('serf', 'NN')] i JJ
[('i', 'JJ'), ('d', 'VBP'), ('like', 'IN'), ('to', 'TO'), ('know', 'VB'), ('what', 'WP'), ('purpose', 'VB'), ('this', 'DT'), ('serf', 'NN')] i JJ
[('i', 'JJ'), ('d', 'VBP'), ('like', 'IN'), ('to', 'TO'), ('know', 'VB'), ('what', 'WP'), ('purpose', 'VB'), ('this', 'DT'), ('serf', 'NN')] i JJ
[('i', 'JJ'), ('d', 'VBP'), ('like', 'IN'), ('to', 'TO'), ('know', 'VB'), ('what', 'WP'), ('purpose', 'VB'), ('this', 'DT'), ('serf', 'NN')] i JJ
[('i', 'JJ'), ('d', 'VBP'), ('like', 'IN'), ('to', 'TO'), ('know', 'VB'), ('what', 'WP'), ('purpose', 'VB'), ('this', 'DT'),

[('ruelle', 'NN'), ('canne', 'NN'), ('sucre', 'NN'), ('prolongue', 'NN'), ('carrefour', 'NN')] ruelle NN
[('ruelle', 'NN'), ('canne', 'NN'), ('sucre', 'NN'), ('prolongue', 'NN'), ('carrefour', 'NN')] ruelle NN
[('ruelle', 'NN'), ('canne', 'NN'), ('sucre', 'NN'), ('prolongue', 'NN'), ('carrefour', 'NN')] ruelle NN
[('ruelle', 'NN'), ('canne', 'NN'), ('sucre', 'NN'), ('prolongue', 'NN'), ('carrefour', 'NN')] ruelle NN
[('ruelle', 'NN'), ('canne', 'NN'), ('sucre', 'NN'), ('prolongue', 'NN'), ('carrefour', 'NN')] ruelle NN
[('ruelle', 'NN'), ('canne', 'NN'), ('sucre', 'NN'), ('prolongue', 'NN'), ('carrefour', 'NN')] ruelle NN
[('ruelle', 'NN'), ('canne', 'NN'), ('sucre', 'NN'), ('prolongue', 'NN'), ('carrefour', 'NN')] ruelle NN
[('ruelle', 'NN'), ('canne', 'NN'), ('sucre', 'NN'), ('prolongue', 'NN'), ('carrefour', 'NN')] ruelle NN
[('ruelle', 'NN'), ('canne', 'NN'), ('sucre', 'NN'), ('prolongue', 'NN'), ('carrefour', 'NN')] ruelle NN
[('ruelle', 'NN'), ('canne', 'NN'), ('sucre', 'NN'), ('

[('we', 'PRP'), ('have', 'VBP'), ('no', 'DT'), ('water', 'NN'), ('food', 'NN'), ('and', 'CC'), ('tent', 'NN')] we PRP
[('we', 'PRP'), ('have', 'VBP'), ('no', 'DT'), ('water', 'NN'), ('food', 'NN'), ('and', 'CC'), ('tent', 'NN')] we PRP
[('we', 'PRP'), ('have', 'VBP'), ('no', 'DT'), ('water', 'NN'), ('food', 'NN'), ('and', 'CC'), ('tent', 'NN')] we PRP
[('we', 'PRP'), ('have', 'VBP'), ('no', 'DT'), ('water', 'NN'), ('food', 'NN'), ('and', 'CC'), ('tent', 'NN')] we PRP
[('we', 'PRP'), ('have', 'VBP'), ('no', 'DT'), ('water', 'NN'), ('food', 'NN'), ('and', 'CC'), ('tent', 'NN')] we PRP
[('we', 'PRP'), ('have', 'VBP'), ('no', 'DT'), ('water', 'NN'), ('food', 'NN'), ('and', 'CC'), ('tent', 'NN')] we PRP
[('we', 'PRP'), ('have', 'VBP'), ('no', 'DT'), ('water', 'NN'), ('food', 'NN'), ('and', 'CC'), ('tent', 'NN')] we PRP
[('we', 'PRP'), ('have', 'VBP'), ('no', 'DT'), ('water', 'NN'), ('food', 'NN'), ('and', 'CC'), ('tent', 'NN')] we PRP
[('we', 'PRP'), ('have', 'VBP'), ('no', 'DT'), ('water',

[('i', 'NN'), ('suffering', 'VBG'), ('from', 'IN'), ('a', 'DT'), ('crush', 'JJ'), ('injury', 'NN'), ('the', 'DT'), ('doctor', 'NN'), ('said', 'VBD'), ('there', 'EX'), ('s', 'JJ'), ('nothing', 'NN'), ('that', 'WDT'), ('can', 'MD'), ('be', 'VB'), ('done', 'VBN'), ('to', 'TO'), ('help', 'VB'), ('me', 'PRP')] i NN
[('i', 'NN'), ('suffering', 'VBG'), ('from', 'IN'), ('a', 'DT'), ('crush', 'JJ'), ('injury', 'NN'), ('the', 'DT'), ('doctor', 'NN'), ('said', 'VBD'), ('there', 'EX'), ('s', 'JJ'), ('nothing', 'NN'), ('that', 'WDT'), ('can', 'MD'), ('be', 'VB'), ('done', 'VBN'), ('to', 'TO'), ('help', 'VB'), ('me', 'PRP')] i NN
[('i', 'NN'), ('suffering', 'VBG'), ('from', 'IN'), ('a', 'DT'), ('crush', 'JJ'), ('injury', 'NN'), ('the', 'DT'), ('doctor', 'NN'), ('said', 'VBD'), ('there', 'EX'), ('s', 'JJ'), ('nothing', 'NN'), ('that', 'WDT'), ('can', 'MD'), ('be', 'VB'), ('done', 'VBN'), ('to', 'TO'), ('help', 'VB'), ('me', 'PRP')] i NN
[('i', 'NN'), ('suffering', 'VBG'), ('from', 'IN'), ('a', 'DT'),

[('as', 'IN'), ('a', 'DT'), ('result', 'NN'), ('a', 'DT'), ('joint', 'JJ'), ('demarche', 'NN'), ('wa', 'NN'), ('made', 'VBD'), ('to', 'TO'), ('the', 'DT'), ('ministry', 'NN'), ('of', 'IN'), ('foreign', 'JJ'), ('affairs', 'NNS'), ('of', 'IN'), ('tajikistan', 'NN'), ('by', 'IN'), ('several', 'JJ'), ('embassies', 'NNS')] as IN
[('as', 'IN'), ('a', 'DT'), ('result', 'NN'), ('a', 'DT'), ('joint', 'JJ'), ('demarche', 'NN'), ('wa', 'NN'), ('made', 'VBD'), ('to', 'TO'), ('the', 'DT'), ('ministry', 'NN'), ('of', 'IN'), ('foreign', 'JJ'), ('affairs', 'NNS'), ('of', 'IN'), ('tajikistan', 'NN'), ('by', 'IN'), ('several', 'JJ'), ('embassies', 'NNS')] as IN
[('as', 'IN'), ('a', 'DT'), ('result', 'NN'), ('a', 'DT'), ('joint', 'JJ'), ('demarche', 'NN'), ('wa', 'NN'), ('made', 'VBD'), ('to', 'TO'), ('the', 'DT'), ('ministry', 'NN'), ('of', 'IN'), ('foreign', 'JJ'), ('affairs', 'NNS'), ('of', 'IN'), ('tajikistan', 'NN'), ('by', 'IN'), ('several', 'JJ'), ('embassies', 'NNS')] as IN
[('as', 'IN'), ('a', '

In [ ]:
category_names = y.columns


y_pred = cv1.predict(X_test)
print(classification_report(y_test, y_pred, target_names=category_names, zero_division=0))

In [ ]:
 for i in range(len(category_names)):
        print("classification report for " + y_test.columns[i]
              , '\n', classification_report(y_test.values[:, i], y_pred[:, i])
              , '\n accuracy:', accuracy_score(y_test.values[:, i], y_pred[:, i]))

### 9. Export your model as a pickle file


In [78]:
pkl_filename = 'sutula_classifier.pkl' 
with open(pkl_filename, 'wb') as file: 
    pickle.dump(cv, file)

SyntaxError: invalid syntax (<ipython-input-78-3f03cd11d98e>, line 1)

In [ ]:
# save the model as a pickle file
filename = 'sutula_classifier.pkl' 
pickle.dump(cv, open(filename, 'wb')) #Saving the model

### 10. Use this notebook to complete train.py

Use the template file attached in the Resources folder to write a script that runs the steps above to create a database and export a model based on a new dataset specified by the user.
